In [2]:
from ioos_qc.config import QcConfig
from ioos_qc import qartod
import xarray as xr
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from datetime import datetime

from bokeh.layouts import gridplot
from bokeh.plotting import figure, show, output_notebook, save
from bokeh.embed import file_html
from bokeh.resources import CDN
from bokeh.io import output_file, show


output_notebook()


ModuleNotFoundError: No module named 'ioos_qc'

In [1]:
def plot_results(data, var_name, results, title, test_name, save_name=None):

    time = data['time']
    obs = data[var_name]
    qc_test = results['qartod'][test_name]

    qc_pass = np.ma.masked_where(qc_test != 1, obs)
    qc_suspect = np.ma.masked_where(qc_test != 3, obs)
    qc_fail = np.ma.masked_where(qc_test != 4, obs)
    qc_notrun = np.ma.masked_where(qc_test != 2, obs)

    p1 = figure(x_axis_type="datetime", title=test_name + ' : ' + title)
    p1.grid.grid_line_alpha=0.3
    p1.xaxis.axis_label = 'Time'
    p1.yaxis.axis_label = 'Observation Value'

    p1.line(time, obs,  legend='obs', color='#A6CEE3')
    p1.circle(time, qc_notrun, size=2, legend='qc not run', color='gray', alpha=0.2)
    p1.circle(time, qc_pass, size=4, legend='qc pass', color='green', alpha=0.5)
    p1.circle(time, qc_suspect, size=4, legend='qc suspect', color='orange', alpha=0.7)
    p1.circle(time, qc_fail, size=6, legend='qc fail', color='red', alpha=1.0)
    if save_name is not None:
        html = file_html(p1, CDN, "my plot")
        with open("./OA_wtemp.html", mode='w') as f:
            f.write(html)
            
    show(gridplot([[p1]], plot_width=800, plot_height=400))

    
def make_dataframe(xr_dataset):
    '''
    Return a pandas dataframe of all of the data, indexed by time.
    This only works for single depth and location data
    '''
    data = {}
    for var in xr_dataset.variables:
        if var not in ['TIME','DEPTH','LATITUDE','LONGITUDE']:
            data[var] = xr_dataset[var].to_pandas()
    return pd.DataFrame(data, index=xr_dataset['TIME'].to_pandas())
    


In [ ]:
ocsd_data_file = '\\sirocco\wwwroot\bog\drifterdata\mbari42\dev\csv\Temperature.csv'
ds = pd.read_csv(ocsd_data_file)
ds = ds.isel(DEPTH=0, LATITUDE=0, LONGITUDE=0) # All data is at the surface
df = make_dataframe(ds)

In [ ]:
df['epoch_time'] = df.index.astype(np.int64) // 10**9
df['time'] = df.index

In [ ]:
df.head()

In [ ]:
data_vars = ['O2_conc','air_temp','atm_press','avg_wind_spd','chl','pCO2_air','pCO2_water','pH','sal','water_temp','wind_dir']
fig, ax = plt.subplots(len(data_vars),sharex=True)
fig.set_size_inches(w=8,h=2.5*len(data_vars))
for i, var in enumerate(data_vars):
    ax[i].plot(df[var],marker='.')
    ax[i].set_ylabel(var)

In [ ]:
fig, ax = plt.subplots()
fig.set_size_inches(8,6)
df['water_temp'].plot(ax=ax)

ax.hlines(17.5,xmin=df.index[0], xmax=df.index[-1])
ax.hlines(12.5,xmin=df.index[0], xmax=df.index[-1])
ax.hlines(20,xmin=df.index[0], xmax=df.index[-1],color='r')
ax.hlines(10,xmin=df.index[0], xmax=df.index[-1],color='r')

In [ ]:
config = {
    'qartod': {
        'gross_range_test': {
            'suspect_span': [12.5, 17.5],
            'fail_span': [10, 20]
        },
        "flat_line_test": {
            "tolerance": 0.01,
            "suspect_threshold": 7200,
            "fail_threshold": 21600
        },
        "rate_of_change_test": {
            "threshold": 0.001
      },
        "spike_test": {
            "suspect_threshold": 0.8,
            "fail_threshold": 3
      }
    }
}
qc = QcConfig(config)

qc_results =  qc.run(
    inp=df['water_temp'],
    tinp=df['epoch_time']
)
all_tests = [qc_results['qartod'][test_name] for test_name in qc_results['qartod'].keys()]
qc_results['qartod']['qc_agg'] = qartod.qartod_compare(all_tests).astype(int)
qc_results

In [ ]:
#results
title = "Seawater Temp: OA1"

plot_results(df, 'water_temp', qc_results, title, 'gross_range_test')
plot_results(df, 'water_temp', qc_results, title, 'flat_line_test')
plot_results(df, 'water_temp', qc_results, title, 'spike_test')
plot_results(df, 'water_temp', qc_results, title, 'rate_of_change_test')

In [ ]:
test_name = "gross_range_test"


time = df['time']
obs = df['water_temp']
qc_test = qc_results['qartod'][test_name]

qc_pass = np.ma.masked_where(qc_test != 1, obs)
qc_suspect = np.ma.masked_where(qc_test != 3, obs)
qc_fail = np.ma.masked_where(qc_test != 4, obs)
qc_notrun = np.ma.masked_where(qc_test != 2, obs)

p1 = figure(x_axis_type="datetime", title=test_name + ' : ' + title)
p1.grid.grid_line_alpha=0.3
p1.xaxis.axis_label = 'Time'
p1.yaxis.axis_label = 'Observation Value'

p1.line(time, obs,  legend='obs', color='#A6CEE3')
p1.circle(time, qc_notrun, size=2, legend='qc not run', color='gray', alpha=0.2)
p1.circle(time, qc_pass, size=4, legend='qc pass', color='green', alpha=0.5)
p1.circle(time, qc_suspect, size=4, legend='qc suspect', color='orange', alpha=0.7)
p1.circle(time, qc_fail, size=6, legend='qc fail', color='red', alpha=1.0)

output_file('plot.html')

show(gridplot([[p1]], plot_width=800, plot_height=400))


In [ ]:
data = {}
for var in ds.variables:
    if var not in ['TIME','DEPTH','LATITUDE','LONGITUDE']:
        data[var] = ds[var].to_pandas()
df = pd.DataFrame(data)

In [ ]:
fig,ax = plt.subplots()
ax.plot(df['avg_wind_spd'].values)

In [ ]:
ds['water_temp'].to_pandas().plot()